In [0]:
spark

SparkSession - hive 
 
 
 SparkContext 

 Spark UI 

 
 Version 
 v3.3.2 
 Master 
 local[8] 
 AppName 
 Databricks Shell

In [0]:
from pyspark.sql.types import StructType, StructField, StringType, TimestampType, DoubleType, IntegerType, DateType

from pyspark.sql.functions import *

In [0]:
# importing Spark session from pyspark.sql
from pyspark.sql import SparkSession 

# Creating Spark Session with Appname
spark = SparkSession.builder.appName("Health Care Data Engineering Spark Project").getOrCreate()

# getOrCreate() this will get the app if created or else it will create a new session

In [0]:
# Creating Structural Schema
# To set a default schema for every data that will be loaded

# Struct Schema for conditions
conditions_schema = StructType([
    StructField("start", TimestampType(),True),
    StructField("stop", TimestampType(),True),
    StructField("patient", StringType(),True),
    StructField("encounter", StringType(),True),
    StructField("code", StringType(),True),
    StructField("description", StringType(),True),
])

encounters_schema = StructType([
    StructField("id", StringType(), True),
    StructField("start", TimestampType(), True),
    StructField("stop", TimestampType(), True),
    StructField("patient", StringType(), True),
    StructField("organization", StringType(), True),
    StructField("provider", StringType(), True),
    StructField("payer", StringType(), True),
    StructField("encounterclass", StringType(), True),
    StructField("code", IntegerType(), True),
    StructField("description", StringType(), True),
    StructField("base_encounter_cost", DoubleType(), True),
    StructField("total_claim_cost", DoubleType(), True),
    StructField("payer_coverage", DoubleType(), True),
    StructField("reasoncode", StringType(), True)
])

# Schema for immunizations_df
immunizations_schema = StructType([
    StructField("date", TimestampType(), True),
    StructField("patient", StringType(), True),
    StructField("encounter", StringType(), True),
    StructField("code", IntegerType(), True),
    StructField("description", StringType(), True)
])

# Schema for patients_df
patients_schema = StructType([
    StructField("id", StringType(), True),
    StructField("birthdate", DateType(), True),
    StructField("deathdate", DateType(), True),
    StructField("ssn", StringType(), True),
    StructField("drivers", StringType(), True),
    StructField("passport", StringType(), True),
    StructField("prefix", StringType(), True),
    StructField("first", StringType(), True),
    StructField("last", StringType(), True),
    StructField("suffix", StringType(), True),
    StructField("maiden", StringType(), True),
    StructField("marital", StringType(), True),
    StructField("race", StringType(), True),
    StructField("ethnicity", StringType(), True),
    StructField("gender", StringType(), True),
    StructField("birthplace", StringType(), True),
    StructField("address", StringType(), True),
    StructField("city", StringType(), True),
    StructField("state", StringType(), True),
    StructField("county", StringType(), True),
    StructField("fips", IntegerType(), True),
    StructField("zip", IntegerType(), True),
    StructField("lat", DoubleType(), True),
    StructField("lon", DoubleType(), True),
    StructField("healthcare_expenses", DoubleType(), True),
    StructField("healthcare_coverage", DoubleType(), True),
    StructField("income", IntegerType(), True),
    StructField("mrn", IntegerType(), True)
])

In [0]:

def load_csv(spark, schema, file_path):
    """
    Load a CSV file from S3 into a Spark DataFrame with the given schema.
    
    Parameters:
        spark (SparkSession): The active Spark session.
        schema (StructType): The schema for the DataFrame.
        file_path (str): The S3 path of the CSV file.
    
    Returns:
        DataFrame: The loaded Spark DataFrame.
    """
    return (spark.read.schema(schema).format("csv").option("header", "true").load(file_path))

# Initialize Spark session
spark = SparkSession.builder.appName("HealthcareDataProcessing").getOrCreate()

# Read Health Data CSV Files from AWS S3 Bucket
# initially AWS S3 Bucket was not public so I changed the bucket policy changed all the block settings from the AWS Console

conditions_df = load_csv(spark, conditions_schema, "s3://health-care-data-bucket/conditions.csv")
encounters_df = load_csv(spark, encounters_schema, "s3://health-care-data-bucket/encounters.csv")
immunizations_df = load_csv(spark, immunizations_schema, "s3://health-care-data-bucket/immunizations.csv")
patients_df = load_csv(spark, patients_schema, "s3://health-care-data-bucket/patients.csv")




In [0]:
patients_df.columns

Out[84]: ['id',
 'birthdate',
 'deathdate',
 'ssn',
 'drivers',
 'passport',
 'prefix',
 'first',
 'last',
 'suffix',
 'maiden',
 'marital',
 'race',
 'ethnicity',
 'gender',
 'birthplace',
 'address',
 'city',
 'state',
 'county',
 'fips',
 'zip',
 'lat',
 'lon',
 'healthcare_expenses',
 'healthcare_coverage',
 'income',
 'mrn']

In [0]:
patients_df.limit(10).display()

patients_df.count()

id birthdate deathdate ssn drivers passport prefix first last suffix maiden marital race ethnicity gender birthplace address city state county fips zip lat lon healthcare_expenses healthcare_coverage income mrn 73d3ebe3-e656-b9de-fd61-88d370a86d51 1985-09-15 null 999-54-9859 S99986862 X21012070X Mrs. Hedy Von NULL Schoen M white nonhispanic F Worcester Massachusetts US 1012 Lueilwitz Trail Unit 2 Reading Massachusetts Middlesex County 25017 1867 42.52496000289047 -71.1210503282821 8522.61 261550.12 8402 1 cc53e99a-6715-603f-b074-eea93fe11e20 1961-07-26 2019-08-17 999-19-2105 S99922222 X66407833X Mrs. Adelina Treutel NULL Miller D white nonhispanic F Scituate Massachusetts US 622 Kilback Loaf Springfield Massachusetts Hampden County 25013 1104 42.09394120412677 -72.5707445727102 824192.36 31979.82 42514 2 15e61a30-618d-4b20-dd5d-5dc627fa6e4c 2001-12-27 null 999-44-5853 S99929170 X68583323X Ms. Artie Cronin NULL NULL NULL white nonhispanic F Brockton Massachusetts US 763 Tillman Junction Worcester Massachusetts Worcester County 25027 1604 42.291968201261824 -71.81152962280308 32502.1 767484.6 638066 3 32a2188a-132e-4fd4-1a0e-3d532f4c4ea8 1958-12-17 null 999-78-8436 S99914103 X28243259X Mrs. Lauryn Wisozk NULL Senger M white hispanic F Fitchburg Massachusetts US 797 Lemke Bypass Unit 25 Boston Massachusetts Suffolk County 25025 2121 42.25729277762842 -71.08346502522105 437107.67 933931.36 147695 4 4adcad4e-1aa5-5601-4107-55953f484703 1962-06-26 null 999-72-3919 S99998121 X76753902X Mrs. Dorthea Reichel NULL McDermott M black nonhispanic F Fall River Massachusetts US 865 Simonis Highlands Suite 83 Braintree Massachusetts Norfolk County 25021 2184 42.23661190444311 -71.00959511002986 254423.25 590863.07 122035 5 52de8610-de40-203d-4bd6-cf06141fa864 1975-11-08 null 999-27-4817 S99922577 X50092027X Mrs. Sherita Orn NULL Huels D white nonhispanic F Northborough Massachusetts US 508 Haag Lock Ludlow Massachusetts Hampden County null 0 42.135095795514815 -72.44664055250006 556114.94 11443.34 55707 6 154290c8-6729-fe33-d3b6-a66f04bb939e 1964-10-02 null 999-12-6101 S99929848 X1401129X Ms. Elenora Raynor NULL NULL S white nonhispanic F Fairhaven Massachusetts US 608 Lind Forge Apt 24 East Sandwich Massachusetts Barnstable County 25001 2537 41.76856882290082 -70.45565220982637 22782.33 958551.12 261849 7 10d940ae-7114-8bcf-50f9-2bfd5354ff41 1962-05-17 null 999-95-9039 S99962381 X43169098X Mrs. Rebeca Mayer NULL Beatty M white nonhispanic F Randolph Massachusetts US 797 Monahan Divide Unit 44 Methuen Massachusetts Essex County 25009 1844 42.70238540126656 -71.19779376499118 654622.19 270730.9 60975 8 ac63da4a-893a-1d3c-aa93-fb78c8da3d95 1971-04-21 null 999-34-2266 S99975964 X17674028X Mrs. Casie Hilpert NULL Friesen M white nonhispanic F Billerica Massachusetts US 715 Mitchell Plaza Dover Massachusetts Norfolk County 25021 2030 42.252071748674375 -71.26056668178677 312357.59 1001217.44 247569 9 bcb267a1-09ab-7082-96bd-81b867c68da7 1983-10-04 null 999-83-2417 S99950708 X82674718X Mrs. Arline Jenkins NULL Beatty M white nonhispanic F Westford Massachusetts US 570 Ryan Station Hanover Massachusetts Plymouth County null 0 42.15780614923903 -70.8831098081869 11404.46 657952.08 17204 10

Out[96]: 11363

In [0]:
# Data Cleaning and Transformation of Patient Dataframe

# standardizing column marital
clean_patients_df = patients_df.withColumn('marital', when(patients_df.marital == 'M', 'Married').when(patients_df.marital == 'S', 'Single').when(patients_df.marital == 'D', 'Divorced').otherwise('n/a'))

new_clean_patients_df = clean_patients_df.withColumn('gender', when(patients_df.gender == 'M', 'Male').when(patients_df.gender == 'F', 'Female').otherwise('n/a'))

new_clean_patients_df.display()

id birthdate deathdate ssn drivers passport prefix first last suffix maiden marital race ethnicity gender birthplace address city state county fips zip lat lon healthcare_expenses healthcare_coverage income mrn 73d3ebe3-e656-b9de-fd61-88d370a86d51 1985-09-15 null 999-54-9859 S99986862 X21012070X Mrs. Hedy Von NULL Schoen Married white nonhispanic Female Worcester Massachusetts US 1012 Lueilwitz Trail Unit 2 Reading Massachusetts Middlesex County 25017 1867 42.52496000289047 -71.1210503282821 8522.61 261550.12 8402 1 cc53e99a-6715-603f-b074-eea93fe11e20 1961-07-26 2019-08-17 999-19-2105 S99922222 X66407833X Mrs. Adelina Treutel NULL Miller Divorced white nonhispanic Female Scituate Massachusetts US 622 Kilback Loaf Springfield Massachusetts Hampden County 25013 1104 42.09394120412677 -72.5707445727102 824192.36 31979.82 42514 2 15e61a30-618d-4b20-dd5d-5dc627fa6e4c 2001-12-27 null 999-44-5853 S99929170 X68583323X Ms. Artie Cronin NULL NULL n/a white nonhispanic Female Brockton Massachusetts US 763 Tillman Junction Worcester Massachusetts Worcester County 25027 1604 42.291968201261824 -71.81152962280308 32502.1 767484.6 638066 3 32a2188a-132e-4fd4-1a0e-3d532f4c4ea8 1958-12-17 null 999-78-8436 S99914103 X28243259X Mrs. Lauryn Wisozk NULL Senger Married white hispanic Female Fitchburg Massachusetts US 797 Lemke Bypass Unit 25 Boston Massachusetts Suffolk County 25025 2121 42.25729277762842 -71.08346502522105 437107.67 933931.36 147695 4 4adcad4e-1aa5-5601-4107-55953f484703 1962-06-26 null 999-72-3919 S99998121 X76753902X Mrs. Dorthea Reichel NULL McDermott Married black nonhispanic Female Fall River Massachusetts US 865 Simonis Highlands Suite 83 Braintree Massachusetts Norfolk County 25021 2184 42.23661190444311 -71.00959511002986 254423.25 590863.07 122035 5 52de8610-de40-203d-4bd6-cf06141fa864 1975-11-08 null 999-27-4817 S99922577 X50092027X Mrs. Sherita Orn NULL Huels Divorced white nonhispanic Female Northborough Massachusetts US 508 Haag Lock Ludlow Massachusetts Hampden County null 0 42.135095795514815 -72.44664055250006 556114.94 11443.34 55707 6 154290c8-6729-fe33-d3b6-a66f04bb939e 1964-10-02 null 999-12-6101 S99929848 X1401129X Ms. Elenora Raynor NULL NULL Single white nonhispanic Female Fairhaven Massachusetts US 608 Lind Forge Apt 24 East Sandwich Massachusetts Barnstable County 25001 2537 41.76856882290082 -70.45565220982637 22782.33 958551.12 261849 7 10d940ae-7114-8bcf-50f9-2bfd5354ff41 1962-05-17 null 999-95-9039 S99962381 X43169098X Mrs. Rebeca Mayer NULL Beatty Married white nonhispanic Female Randolph Massachusetts US 797 Monahan Divide Unit 44 Methuen Massachusetts Essex County 25009 1844 42.70238540126656 -71.19779376499118 654622.19 270730.9 60975 8 ac63da4a-893a-1d3c-aa93-fb78c8da3d95 1971-04-21 null 999-34-2266 S99975964 X17674028X Mrs. Casie Hilpert NULL Friesen Married white nonhispanic Female Billerica Massachusetts US 715 Mitchell Plaza Dover Massachusetts Norfolk County 25021 2030 42.252071748674375 -71.26056668178677 312357.59 1001217.44 247569 9 bcb267a1-09ab-7082-96bd-81b867c68da7 1983-10-04 null 999-83-2417 S99950708 X82674718X Mrs. Arline Jenkins NULL Beatty Married white nonhispanic Female Westford Massachusetts US 570 Ryan Station Hanover Massachusetts Plymouth County null 0 42.15780614923903 -70.8831098081869 11404.46 657952.08 17204 10 91f57fef-7f76-6f23-1c4b-eb973e556ce3 1983-05-27 null 999-57-2760 S99911251 X20307042X Ms. Rosario Ruecker NULL NULL Single white nonhispanic Female Chesterfield Massachusetts US 317 Crist Light Quincy Massachusetts Norfolk County 25021 2169 42.19968342314834 -71.04747202133595 303222.66 1008151.05 135246 11 f8f224ae-59fb-ae53-d1a3-50e56341e844 1967-08-12 2020-02-13 999-31-9442 S99994622 X39515782X Ms. Ngoc Willms NULL NULL Single white nonhispanic Female Ipswich Massachusetts US 1098 Schultz Trace Unit 28 Somerville Massachusetts Middlesex County 25017 2138 42.427245566358366 -71.09643440850698 256229.95 649362.44 757056 12 ea264f1c-04e6-c056-54e7-5d5c63a6fc4c 20

In [0]:
# Register DataFrames as SQL Views
conditions_df.createOrReplaceTempView("conditions")
encounters_df.createOrReplaceTempView("encounters")
immunizations_df.createOrReplaceTempView("immunizations")
patients_df.createOrReplaceTempView("patients")

In [0]:
condi_df = spark.sql(
    """
    SELECT min(birthdate),max(birthdate)  FROM patients
    """
)

condi_df.display()

min(birthdate) max(birthdate) 1912-12-25 2023-06-02

In [0]:
condi_df = patients_df.select(min("birthdate").alias("min_birthdate"), 
                              max("birthdate").alias("max_birthdate"))

condi_df.display()

min_birthdate max_birthdate 1912-12-25 2023-06-02

In [0]:
condi_df = patients_df.agg(
    min("birthdate").alias("min_birthdate"),
    max("birthdate").alias("max_birthdate")
)

# Show the result
condi_df.display()

min_birthdate max_birthdate 1912-12-25 2023-06-02

In [0]:
conditions_df.show(5)

+-------------------+-------------------+--------------------+--------------------+------+--------------------+
|              start|               stop|             patient|           encounter|  code|         description|
+-------------------+-------------------+--------------------+--------------------+------+--------------------+
|1953-06-03 00:00:00|               null|531997f3-3373-058...|b67eb71d-01d4-e22...| 473.8|Other chronic sin...|
|1952-03-12 00:00:00|               null|12556183-9867-11e...|56c1ae8b-c774-025...| 473.9|Unspecified sinus...|
|1957-10-09 00:00:00|               null|82e05bd5-78f8-2fe...|5f37acfc-84c0-7ba...| V60.9|Unspecified housi...|
|1954-02-13 00:00:00|1956-02-25 00:00:00|63dc3aeb-c77c-441...|4c822b22-96ee-f96...|V62.89|Other psychologic...|
|1951-09-13 00:00:00|               null|d70308e9-5bce-115...|9967cce2-0a85-9dc...|   541|Appendicitis, unq...|
+-------------------+-------------------+--------------------+--------------------+------+--------------

In [0]:
encounters_df.show(5)

+--------------------+-------------------+-------------------+--------------------+--------------------+--------------------+--------------------+--------------+----+--------------------+-------------------+----------------+--------------+----------+
|                  id|              start|               stop|             patient|        organization|            provider|               payer|encounterclass|code|         description|base_encounter_cost|total_claim_cost|payer_coverage|reasoncode|
+--------------------+-------------------+-------------------+--------------------+--------------------+--------------------+--------------------+--------------+----+--------------------+-------------------+----------------+--------------+----------+
|be86bb53-1982-c56...|2018-04-07 21:17:11|2018-04-07 21:32:11|bb8d3c0d-78f6-747...|9d0e702d-50a0-3f4...|179a5ef5-b06b-39c...|8fa6c185-e44e-3e3...|    ambulatory|1032|Hospital Encounte...|              85.55|           85.55|           0.0|      NU

In [0]:
immunizations_df.show(5)

+-------------------+--------------------+--------------------+----+--------------------+
|               date|             patient|           encounter|code|         description|
+-------------------+--------------------+--------------------+----+--------------------+
|2011-07-27 14:09:40|cc53e99a-6715-603...|ac02e16e-618c-e24...|5301|Herpes Zoster Vac...|
|2011-07-27 14:09:40|cc53e99a-6715-603...|ac02e16e-618c-e24...|5302|Seasonal Flu Vaccine|
|2013-12-09 04:14:13|73d3ebe3-e656-b9d...|2bb23033-f5e9-024...|5302|Seasonal Flu Vaccine|
|2014-12-15 04:14:13|73d3ebe3-e656-b9d...|570d34ce-6c5d-bbb...|5302|Seasonal Flu Vaccine|
|2012-08-01 14:09:40|cc53e99a-6715-603...|fa522491-1733-394...|5301|Herpes Zoster Vac...|
+-------------------+--------------------+--------------------+----+--------------------+
only showing top 5 rows



In [0]:
patients_df.show(5) 

+--------------------+----------+----------+-----------+---------+----------+------+-------+-------+------+---------+-------+-----+-----------+------+--------------------+--------------------+-----------+-------------+----------------+-----+----+------------------+------------------+-------------------+-------------------+------+---+
|                  id| birthdate| deathdate|        ssn|  drivers|  passport|prefix|  first|   last|suffix|   maiden|marital| race|  ethnicity|gender|          birthplace|             address|       city|        state|          county| fips| zip|               lat|               lon|healthcare_expenses|healthcare_coverage|income|mrn|
+--------------------+----------+----------+-----------+---------+----------+------+-------+-------+------+---------+-------+-----+-----------+------+--------------------+--------------------+-----------+-------------+----------------+-----+----+------------------+------------------+-------------------+-------------------+----

In [0]:
patients_df.columns

Out[42]: ['id',
 'birthdate',
 'deathdate',
 'ssn',
 'drivers',
 'passport',
 'prefix',
 'first',
 'last',
 'suffix',
 'maiden',
 'marital',
 'race',
 'ethnicity',
 'gender',
 'birthplace',
 'address',
 'city',
 'state',
 'county',
 'fips',
 'zip',
 'lat',
 'lon',
 'healthcare_expenses',
 'healthcare_coverage',
 'income',
 'mrn']

In [0]:
df = patients_df[['id']]

In [0]:
df.show(5)

+--------------------+
|                  id|
+--------------------+
|73d3ebe3-e656-b9d...|
|cc53e99a-6715-603...|
|15e61a30-618d-4b2...|
|32a2188a-132e-4fd...|
|4adcad4e-1aa5-560...|
+--------------------+
only showing top 5 rows

